# np.roll 활용 data augmentation
 - 참조  
 https://dacon.io/competitions/official/235689/codeshare/2347?page=1&dtype=recent&ptype=pub
 https://dacon.io/competitions/official/235689/codeshare/2306?page=1&dtype=recent&ptype=pub

## np.roll -> shifted data -> new DataFrame

In [1]:
import pandas as pd
import numpy as np
import random
import matplotlib.pyplot as plt
from tqdm import tqdm
from glob import glob

In [2]:
import matplotlib.pyplot as plt
import seaborn as sns

In [3]:
from tqdm import tqdm_notebook as tn

In [53]:
train_features = pd.read_csv('train_features.csv')
train_labels = pd.read_csv('train_labels.csv')
test = pd.read_csv('test_features.csv')
submission = pd.read_csv('sample_submission.csv')

In [94]:
submission = pd.read_csv('sample_submission.csv')

In [54]:
TL = train_labels[['id','label']]

In [55]:
train = pd.merge(train_features,TL, how = 'left', on = 'id')

In [56]:
train.head()

id  time     acc_x     acc_y     acc_z      gy_x       gy_y       gy_z  \
0   0     0  1.206087 -0.179371 -0.148447 -0.591608 -30.549010 -31.676112   
1   0     1  1.287696 -0.198974 -0.182444  0.303100 -39.139103 -24.927216   
2   0     2  1.304609 -0.195114 -0.253382 -3.617278 -44.122565 -25.019629   
3   0     3  1.293095 -0.230366 -0.215210  2.712986 -53.597843 -27.454013   
4   0     4  1.300887 -0.187757 -0.222523  4.286707 -57.906561 -27.961234   

   label  
0     37  
1     37  
2     37  
3     37  
4     37

In [57]:
Label_counts = pd.DataFrame(TL['label'].value_counts())

In [58]:
TL['label'].value_counts()

26    1518
8       97
28      55
60      48
18      47
      ... 
53      13
52      12
13      12
12      12
0       12
Name: label, Length: 61, dtype: int64

# <font bord>label 개수 확인 n개보다 적으면 augmentation</font>
 1. lable 개수 확인(<n)
 2. augmentation할 label 저장(list)
 3. label 하나씩 dataframe 불러오기
 4. 불러온 data id 개수 확인
 5. id 한개당 몇개의 shifted data 만들지 계산
     - 한개당 -> int(500/id) - shift(15씩)
 6. shift data -> data frame 변환 id,labe,time등 지정
 7. all_shift에 concat하기

In [59]:
n = 300

In [60]:
#1.
def check_label(data, label, num):
    tem = data[data['label'] == label]
    if len(tem['id'].unique())<num:
        return True
    else : return False

In [61]:
# 데이터 변환
def make_train_data(data):
    train_features = data
    x_train = []

    for uid in tqdm(train_features['id'].unique()):
        temp = np.array(train_features[train_features['id'] == uid].iloc[:,2:], np.float32).T
        x_train.append(temp)

    x_train = np.array(x_train, np.float32)
    x_train = x_train[:,:,:,np.newaxis]
    
    return x_train

In [62]:
#2.
small_label = []
for i in tn(list(train_labels['label'].unique())):
    if check_label(train_labels,i,n):
        small_label.append(i)

c:\anaconda3\lib\site-packages\ipykernel_launcher.py:3: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  This is separate from the ipykernel package so we can avoid doing imports until


In [63]:
#.데이터 프레임으로 변환
def make_shifted_data(train_data, shift_num,new_id):
    shift_data =  np.roll(train_data, shift_num, axis=2)
    time = list(range(0,600))
    a = pd.DataFrame()
    a['acc_x'] = list(shift_data[0][0].reshape(1,-1)[0])
    a['acc_y'] = list(shift_data[0][1].reshape(1,-1)[0])
    a['acc_z'] = list(shift_data[0][2].reshape(1,-1)[0])
    a['gy_x'] = list(shift_data[0][3].reshape(1,-1)[0])
    a['gy_y'] = list(shift_data[0][4].reshape(1,-1)[0])
    a['gy_z'] = list(shift_data[0][5].reshape(1,-1)[0])
    a['label'] = list(shift_data[0][6].reshape(1,-1)[0])
    a['id'] = new_id
    a['time'] = time
    return a

In [64]:
total_shift_data = pd.DataFrame()

In [65]:
def change_col1(X_train):
    col_name = []
    for i in range(len(X_train.columns)):
        tm_str = '0/0'+X_train.columns[i][0] + '_' + X_train.columns[i][1]
        col_name.append(tm_str)
    X_train.columns = col_name
    return X_train

In [66]:
features = ['id', 'acc_x', 'acc_y', 'acc_z', 'gy_x', 'gy_y', 'gy_z']
add_col = []
for i in range(0,1):
    tm_data = train_features[train_features['id'] == i]
    for j in tn([2,4,8]):
        start_num = 0
        for k in range(1,j+1):
            split_num = int(600 * k / j)
            tm_data2 = tm_data.iloc[start_num:split_num,:]
            tm_train = tm_data2[features].groupby('id').agg(['max', 'min', 'mean','std'])
            
            for q in range(len(tm_train.columns)):
                tm_str = str(k)+'/'+str(j)+tm_train.columns[q][0] + '_' + tm_train.columns[q][1]
                add_col.append(tm_str)
            start_num = split_num

c:\anaconda3\lib\site-packages\ipykernel_launcher.py:5: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  """


In [67]:
def add_FE(tm_data,df,id_):
    features = ['id', 'acc_x', 'acc_y', 'acc_z', 'gy_x', 'gy_y', 'gy_z']
    for j in [2,4,8]:
        start_num = 0
        for k in range(1,j+1):
            split_num = int(600 * k / j)
            tm_data2 = tm_data.iloc[start_num:split_num,:]
            tm_train = tm_data2[features].groupby('id').agg(['max', 'min', 'mean','std'])
            tm_col = []
            for q in range(len(tm_train.columns)):
                tm_str = str(k)+'/'+str(j)+tm_train.columns[q][0] + '_' + tm_train.columns[q][1]
                tm_col.append(tm_str)
            df.loc[id_,tm_col[0]:tm_col[-1]] = list(tm_train.iloc[0,:])
            tm_col = []
            start_num = split_num
    return df

In [ ]:
#3 ~ 7.
features = ['id', 'acc_x', 'acc_y', 'acc_z', 'gy_x', 'gy_y', 'gy_z']
new_id = 1000
for b in tn(small_label):
    print('label, ',i,"진행중")
    tem_data = train[train['label'] == i]
    id_num = list(tem_data['id'].unique())
    how_many_shift = int(n/len(id_num))
    for k in id_num:
        tem_id_data = tem_data[tem_data['id'] == k]
        train_data = make_train_data(tem_id_data)
        for j in range(1,how_many_shift+1):
            shift_num = 19 * j
            shifted_data = make_shifted_data(train_data, shift_num,new_id)
#             print(shifted_data.shape)
            X_train = shifted_data[features].groupby('id').agg(['max', 'min', 'mean','std'])
            X_train = change_col1(X_train)
            for i in add_col:
                X_train[i] = 0
#             print(X_train.iloc[0,:])
            X_train = add_FE(shifted_data,X_train,new_id)                   
#             print(X_train.iloc[0,:])
            
            X_train['label'] = b
            
#             ch_col = []
#             for i in list(X_train.columns):
#                 if i[2] != '0' and i[-3:] == 'ean':
#                     ch_col.append(i)
#             X_train['std1'] = X_train[[ch_col[0],ch_col[6]]].std(1)
#             X_train['std2'] = X_train[[ch_col[1],ch_col[7]]].std(1)
#             X_train['std3'] = X_train[[ch_col[2],ch_col[8]]].std(1)
#             X_train['std4'] = X_train[[ch_col[3],ch_col[9]]].std(1)
#             X_train['std5'] = X_train[[ch_col[4],ch_col[10]]].std(1)
#             X_train['std6'] = X_train[[ch_col[5],ch_col[11]]].std(1)
#             X_train['std7'] = X_train[[ch_col[12],ch_col[18],ch_col[24],ch_col[30]]].std(1)
#             X_train['std8'] = X_train[[ch_col[13],ch_col[19],ch_col[25],ch_col[31]]].std(1)
#             X_train['std9'] = X_train[[ch_col[14],ch_col[20],ch_col[26],ch_col[32]]].std(1)
#             X_train['std10'] = X_train[[ch_col[15],ch_col[21],ch_col[27],ch_col[33]]].std(1)
#             X_train['std11'] = X_train[[ch_col[16],ch_col[22],ch_col[28],ch_col[34]]].std(1)
#             X_train['std12'] = X_train[[ch_col[17],ch_col[23],ch_col[29],ch_col[35]]].std(1)
#             X_train['std13'] = X_train[[ch_col[36],ch_col[42],ch_col[48],ch_col[54],ch_col[60],ch_col[66],ch_col[72],ch_col[78]]].std(1)
#             X_train['std14'] = X_train[[ch_col[37],ch_col[43],ch_col[49],ch_col[55],ch_col[61],ch_col[67],ch_col[73],ch_col[79]]].std(1)
#             X_train['std15'] = X_train[[ch_col[38],ch_col[44],ch_col[50],ch_col[56],ch_col[62],ch_col[68],ch_col[74],ch_col[80]]].std(1)
#             X_train['std16'] = X_train[[ch_col[39],ch_col[45],ch_col[51],ch_col[57],ch_col[63],ch_col[69],ch_col[75],ch_col[81]]].std(1)
#             X_train['std17'] = X_train[[ch_col[40],ch_col[46],ch_col[52],ch_col[58],ch_col[64],ch_col[70],ch_col[76],ch_col[82]]].std(1)
#             X_train['std18'] = X_train[[ch_col[41],ch_col[47],ch_col[53],ch_col[59],ch_col[65],ch_col[71],ch_col[77],ch_col[83]]].std(1)
            
#             X_train['std_max_col'] = 0
#             X_train['std_min_col'] = 0
            
#             tm_l = list(X_train.loc[new_id,'std1':'std18'])
#             X_train.loc[new_id,'std_max_col'] = tm_l.index(max(tm_l))
#             X_train.loc[new_id,'std_min_col'] = tm_l.index(min(tm_l))

            total_shift_data = pd.concat([total_shift_data,X_train])
            print(total_shift_data.shape)
        new_id+=1

In [ ]:
X_train

In [ ]:
total_shift_data.to_csv('a.csv',index = False)

In [ ]:
total_shift_data.head()

In [ ]:
len(total_shift_data.index.unique())

In [ ]:
total_shift_data.shape

In [ ]:
small_label

In [33]:
train['label'] = train_labels['label']

In [29]:
train = train_features

In [46]:
train

id  time     acc_x     acc_y     acc_z       gy_x        gy_y  \
0           0     0  1.206087 -0.179371 -0.148447  -0.591608  -30.549010   
1           0     1  1.287696 -0.198974 -0.182444   0.303100  -39.139103   
2           0     2  1.304609 -0.195114 -0.253382  -3.617278  -44.122565   
3           0     3  1.293095 -0.230366 -0.215210   2.712986  -53.597843   
4           0     4  1.300887 -0.187757 -0.222523   4.286707  -57.906561   
...       ...   ...       ...       ...       ...        ...         ...   
1874995  3124   595 -0.712530 -0.658357  0.293707 -29.367857 -104.013664   
1874996  3124   596 -0.683037 -0.658466  0.329223 -30.149089 -101.796809   
1874997  3124   597 -0.664730 -0.666625  0.364114 -27.873095  -98.776072   
1874998  3124   598 -0.630534 -0.682565  0.373696 -23.636550  -99.139495   
1874999  3124   599 -0.578351 -0.700235  0.384390 -17.917626 -100.181873   

              gy_z  label  
0       -31.676112   37.0  
1       -24.927216   26.0  
2       -25.019629    3.0  
3       -27.454013   26.0  
4       -27.961234   26.0  
...            ...    ...  
1874995 -76.290437    NaN  
1874996 -76.625087    NaN  
1874997 -79.365125    NaN  
1874998 -80.259478    NaN  
1874999 -80.676229    NaN  

[1875000 rows x 9 columns]

In [44]:
tem_data

id  time     acc_x     acc_y     acc_z        gy_x        gy_y  \
0      0     0  1.206087 -0.179371 -0.148447   -0.591608  -30.549010   
64     0    64  1.070323 -0.231747 -0.279709    2.739411   14.668127   
298    0   298  0.921894 -0.402648 -0.230881   -1.078134   -1.446704   
299    0   299  0.993541 -0.416030 -0.251498   -5.305807   -2.733833   
302    0   302  0.983170 -0.427382 -0.237062   -3.189576   -6.878732   
325    0   325  0.874229 -0.314970 -0.390248    6.790756   -4.581029   
450    0   450  0.646232  0.094536 -0.595250    8.835763   -5.055425   
463    0   463  0.741716 -0.023690 -0.540083    2.001787  -16.821605   
557    0   557  0.833069 -0.053138 -0.512256  -11.536337  -15.004510   
606    1     6 -0.158589 -0.029310  0.854627    7.590297   -1.815039   
615    1    15 -0.187117 -0.012583  0.836945  -15.968955   -5.525134   
777    1   177 -1.255099  0.397636 -0.178592  109.192831  173.342948   
986    1   386 -1.008253 -0.682540 -0.363817 -155.501502  -60.999331   
1046   1   446 -0.879216 -0.359580 -0.210028   -4.836686   27.185200   
1073   1   473 -0.962849  0.038447 -0.696718    9.080731   25.876653   
1196   1   596  0.044738 -0.748968  0.748747   44.251607   10.439281   
1214   2    14  0.872942 -0.055581  0.551220  -18.241514 -167.152676   
1236   2    36  0.825736 -0.119836  0.241588   -8.801861    4.083997   
1273   2    73 -0.112254  0.215471  0.924364   45.797373  104.617132   
1277   2    77 -0.751040  0.100176  0.668587   73.525082  115.566155   
1375   2   175  1.023349 -0.046646  0.296671  -10.065726   -4.374089   
1531   2   331  0.592905 -0.036432  0.792338  -45.216103  164.510063   
1565   2   365 -0.750091  0.000054  0.534813  -21.341826   52.956758   
1594   2   394 -0.745875 -0.124380  0.567649  -16.898688 -180.119265   
1816   3    16 -0.679208 -0.467542  0.172533  100.841364   71.538105   
1866   3    66 -1.037061 -0.201445  0.115768   -3.340408   46.533149   
2372   3   572 -0.910433 -0.158983  0.203861  109.071962   86.809167   
2521   4   121 -0.286521 -0.777323  0.206048   37.913924   51.074053   
2641   4   241 -0.787595 -0.283883  0.104188  515.974614   22.509219   
2714   4   314 -0.999958 -0.338904 -0.388099  -28.646957   48.796073   
2756   4   356 -1.059616 -0.141478  0.108978  -27.094553    2.244624   
2781   4   381 -0.985673  0.084310  0.373900   39.732448   -2.896008   
2782   4   382 -1.000593  0.095640  0.385909   48.283797    1.426035   
3009   5     9 -1.281742  0.135419  0.106292  102.661351   -6.395844   
3053   5    53 -0.976621 -0.337722 -0.029373   59.649608   31.738313   

            gy_z  label  
0     -31.676112   37.0  
64     25.816193   37.0  
298   -12.596555   37.0  
299   -14.753329   37.0  
302   -18.510271   37.0  
325   -13.607798   37.0  
450    -2.806143   37.0  
463     4.412009   37.0  
557    -6.135107   37.0  
606    -2.296955   37.0  
615    -3.876089   37.0  
777    72.627961   37.0  
986   -46.456712   37.0  
1046    6.669259   37.0  
1073    1.299114   37.0  
1196   -6.583493   37.0  
1214    7.335118   37.0  
1236    3.853715   37.0  
1273   18.768404   37.0  
1277   13.306955   37.0  
1375   12.000541   37.0  
1531   -5.727448   37.0  
1565    6.056534   37.0  
1594  -31.426896   37.0  
1816   10.889692   37.0  
1866   29.976086   37.0  
2372  -30.617118   37.0  
2521   39.040449   37.0  
2641  117.288728   37.0  
2714   -5.998887   37.0  
2756   25.838688   37.0  
2781    5.610447   37.0  
2782    5.003836   37.0  
3009  -89.360935   37.0  
3053  -29.046494   37.0

In [47]:
small_label

[37,
 3,
 39,
 28,
 6,
 60,
 35,
 34,
 30,
 59,
 15,
 40,
 50,
 48,
 8,
 54,
 16,
 4,
 58,
 21,
 18,
 51,
 25,
 24,
 17,
 49,
 47,
 27,
 36,
 2,
 38,
 14,
 10,
 55,
 57,
 0,
 1,
 46,
 43,
 52,
 53,
 5,
 56,
 23,
 44,
 42,
 19,
 32,
 45,
 29,
 31,
 11,
 7,
 41,
 12,
 9,
 20,
 13,
 22,
 33]

In [49]:
train_data

array([[[[ 1.2060866e+00],
         [ 1.0703231e+00],
         [ 9.2189389e-01],
         [ 9.9354148e-01],
         [ 9.8317045e-01],
         [ 8.7422889e-01],
         [ 6.4623213e-01],
         [ 7.4171650e-01],
         [ 8.3306867e-01]],

        [[-1.7937143e-01],
         [-2.3174657e-01],
         [-4.0264818e-01],
         [-4.1603014e-01],
         [-4.2738169e-01],
         [-3.1496981e-01],
         [ 9.4535604e-02],
         [-2.3689995e-02],
         [-5.3137813e-02]],

        [[-1.4844666e-01],
         [-2.7970928e-01],
         [-2.3088084e-01],
         [-2.5149840e-01],
         [-2.3706232e-01],
         [-3.9024758e-01],
         [-5.9525013e-01],
         [-5.4008311e-01],
         [-5.1225644e-01]],

        [[-5.9160787e-01],
         [ 2.7394109e+00],
         [-1.0781343e+00],
         [-5.3058071e+00],
         [-3.1895757e+00],
         [ 6.7907562e+00],
         [ 8.8357630e+00],
         [ 2.0017867e+00],
         [-1.1536337e+01]],

        [[-3.0549009

In [51]:
tem_data

id  time     acc_x     acc_y     acc_z        gy_x        gy_y  \
0      0     0  1.206087 -0.179371 -0.148447   -0.591608  -30.549010   
64     0    64  1.070323 -0.231747 -0.279709    2.739411   14.668127   
298    0   298  0.921894 -0.402648 -0.230881   -1.078134   -1.446704   
299    0   299  0.993541 -0.416030 -0.251498   -5.305807   -2.733833   
302    0   302  0.983170 -0.427382 -0.237062   -3.189576   -6.878732   
325    0   325  0.874229 -0.314970 -0.390248    6.790756   -4.581029   
450    0   450  0.646232  0.094536 -0.595250    8.835763   -5.055425   
463    0   463  0.741716 -0.023690 -0.540083    2.001787  -16.821605   
557    0   557  0.833069 -0.053138 -0.512256  -11.536337  -15.004510   
606    1     6 -0.158589 -0.029310  0.854627    7.590297   -1.815039   
615    1    15 -0.187117 -0.012583  0.836945  -15.968955   -5.525134   
777    1   177 -1.255099  0.397636 -0.178592  109.192831  173.342948   
986    1   386 -1.008253 -0.682540 -0.363817 -155.501502  -60.999331   
1046   1   446 -0.879216 -0.359580 -0.210028   -4.836686   27.185200   
1073   1   473 -0.962849  0.038447 -0.696718    9.080731   25.876653   
1196   1   596  0.044738 -0.748968  0.748747   44.251607   10.439281   
1214   2    14  0.872942 -0.055581  0.551220  -18.241514 -167.152676   
1236   2    36  0.825736 -0.119836  0.241588   -8.801861    4.083997   
1273   2    73 -0.112254  0.215471  0.924364   45.797373  104.617132   
1277   2    77 -0.751040  0.100176  0.668587   73.525082  115.566155   
1375   2   175  1.023349 -0.046646  0.296671  -10.065726   -4.374089   
1531   2   331  0.592905 -0.036432  0.792338  -45.216103  164.510063   
1565   2   365 -0.750091  0.000054  0.534813  -21.341826   52.956758   
1594   2   394 -0.745875 -0.124380  0.567649  -16.898688 -180.119265   
1816   3    16 -0.679208 -0.467542  0.172533  100.841364   71.538105   
1866   3    66 -1.037061 -0.201445  0.115768   -3.340408   46.533149   
2372   3   572 -0.910433 -0.158983  0.203861  109.071962   86.809167   
2521   4   121 -0.286521 -0.777323  0.206048   37.913924   51.074053   
2641   4   241 -0.787595 -0.283883  0.104188  515.974614   22.509219   
2714   4   314 -0.999958 -0.338904 -0.388099  -28.646957   48.796073   
2756   4   356 -1.059616 -0.141478  0.108978  -27.094553    2.244624   
2781   4   381 -0.985673  0.084310  0.373900   39.732448   -2.896008   
2782   4   382 -1.000593  0.095640  0.385909   48.283797    1.426035   
3009   5     9 -1.281742  0.135419  0.106292  102.661351   -6.395844   
3053   5    53 -0.976621 -0.337722 -0.029373   59.649608   31.738313   

            gy_z  label  
0     -31.676112   37.0  
64     25.816193   37.0  
298   -12.596555   37.0  
299   -14.753329   37.0  
302   -18.510271   37.0  
325   -13.607798   37.0  
450    -2.806143   37.0  
463     4.412009   37.0  
557    -6.135107   37.0  
606    -2.296955   37.0  
615    -3.876089   37.0  
777    72.627961   37.0  
986   -46.456712   37.0  
1046    6.669259   37.0  
1073    1.299114   37.0  
1196   -6.583493   37.0  
1214    7.335118   37.0  
1236    3.853715   37.0  
1273   18.768404   37.0  
1277   13.306955   37.0  
1375   12.000541   37.0  
1531   -5.727448   37.0  
1565    6.056534   37.0  
1594  -31.426896   37.0  
1816   10.889692   37.0  
1866   29.976086   37.0  
2372  -30.617118   37.0  
2521   39.040449   37.0  
2641  117.288728   37.0  
2714   -5.998887   37.0  
2756   25.838688   37.0  
2781    5.610447   37.0  
2782    5.003836   37.0  
3009  -89.360935   37.0  
3053  -29.046494   37.0

In [52]:
train

id  time     acc_x     acc_y     acc_z       gy_x        gy_y  \
0           0     0  1.206087 -0.179371 -0.148447  -0.591608  -30.549010   
1           0     1  1.287696 -0.198974 -0.182444   0.303100  -39.139103   
2           0     2  1.304609 -0.195114 -0.253382  -3.617278  -44.122565   
3           0     3  1.293095 -0.230366 -0.215210   2.712986  -53.597843   
4           0     4  1.300887 -0.187757 -0.222523   4.286707  -57.906561   
...       ...   ...       ...       ...       ...        ...         ...   
1874995  3124   595 -0.712530 -0.658357  0.293707 -29.367857 -104.013664   
1874996  3124   596 -0.683037 -0.658466  0.329223 -30.149089 -101.796809   
1874997  3124   597 -0.664730 -0.666625  0.364114 -27.873095  -98.776072   
1874998  3124   598 -0.630534 -0.682565  0.373696 -23.636550  -99.139495   
1874999  3124   599 -0.578351 -0.700235  0.384390 -17.917626 -100.181873   

              gy_z  label  
0       -31.676112   37.0  
1       -24.927216   26.0  
2       -25.019629    3.0  
3       -27.454013   26.0  
4       -27.961234   26.0  
...            ...    ...  
1874995 -76.290437    NaN  
1874996 -76.625087    NaN  
1874997 -79.365125    NaN  
1874998 -80.259478    NaN  
1874999 -80.676229    NaN  

[1875000 rows x 9 columns]

In [68]:
#3 ~ 7.
features = ['id', 'acc_x', 'acc_y', 'acc_z', 'gy_x', 'gy_y', 'gy_z']
new_id = 1000
d = []
for b in tn(small_label):
    print('label, ',i,"진행중")
    tem_data = train[train['label'] == b]
    id_num = list(tem_data['id'].unique())
    how_many_shift = int(n/len(id_num))
    for k in id_num:
        tem_id_data = tem_data[tem_data['id'] == k]
        train_data = make_train_data(tem_id_data)
        for j in range(1,how_many_shift+1):
            shift_num = 19 * j
            shifted_data = make_shifted_data(train_data, shift_num,new_id)
#             print(shifted_data.shape)
            q_train = shifted_data[features].groupby('id').agg(['max'])
#             X_train = change_col1(X_train)
#             for i in add_col:
#                 X_train[i] = 0
#             print(X_train.iloc[0,:])
#             X_train = add_FE(shifted_data,X_train,new_id)                   
#             print(X_train.iloc[0,:])
            
    
            
#             ch_col = []
#             for i in list(X_train.columns):
#                 if i[2] != '0' and i[-3:] == 'ean':
#                     ch_col.append(i)
#             X_train['std1'] = X_train[[ch_col[0],ch_col[6]]].std(1)
#             X_train['std2'] = X_train[[ch_col[1],ch_col[7]]].std(1)
#             X_train['std3'] = X_train[[ch_col[2],ch_col[8]]].std(1)
#             X_train['std4'] = X_train[[ch_col[3],ch_col[9]]].std(1)
#             X_train['std5'] = X_train[[ch_col[4],ch_col[10]]].std(1)
#             X_train['std6'] = X_train[[ch_col[5],ch_col[11]]].std(1)
#             X_train['std7'] = X_train[[ch_col[12],ch_col[18],ch_col[24],ch_col[30]]].std(1)
#             X_train['std8'] = X_train[[ch_col[13],ch_col[19],ch_col[25],ch_col[31]]].std(1)
#             X_train['std9'] = X_train[[ch_col[14],ch_col[20],ch_col[26],ch_col[32]]].std(1)
#             X_train['std10'] = X_train[[ch_col[15],ch_col[21],ch_col[27],ch_col[33]]].std(1)
#             X_train['std11'] = X_train[[ch_col[16],ch_col[22],ch_col[28],ch_col[34]]].std(1)
#             X_train['std12'] = X_train[[ch_col[17],ch_col[23],ch_col[29],ch_col[35]]].std(1)
#             X_train['std13'] = X_train[[ch_col[36],ch_col[42],ch_col[48],ch_col[54],ch_col[60],ch_col[66],ch_col[72],ch_col[78]]].std(1)
#             X_train['std14'] = X_train[[ch_col[37],ch_col[43],ch_col[49],ch_col[55],ch_col[61],ch_col[67],ch_col[73],ch_col[79]]].std(1)
#             X_train['std15'] = X_train[[ch_col[38],ch_col[44],ch_col[50],ch_col[56],ch_col[62],ch_col[68],ch_col[74],ch_col[80]]].std(1)
#             X_train['std16'] = X_train[[ch_col[39],ch_col[45],ch_col[51],ch_col[57],ch_col[63],ch_col[69],ch_col[75],ch_col[81]]].std(1)
#             X_train['std17'] = X_train[[ch_col[40],ch_col[46],ch_col[52],ch_col[58],ch_col[64],ch_col[70],ch_col[76],ch_col[82]]].std(1)
#             X_train['std18'] = X_train[[ch_col[41],ch_col[47],ch_col[53],ch_col[59],ch_col[65],ch_col[71],ch_col[77],ch_col[83]]].std(1)
            
#             X_train['std_max_col'] = 0
#             X_train['std_min_col'] = 0
            
#             tm_l = list(X_train.loc[new_id,'std1':'std18'])
#             X_train.loc[new_id,'std_max_col'] = tm_l.index(max(tm_l))
#             X_train.loc[new_id,'std_min_col'] = tm_l.index(min(tm_l))

#             total_shift_data = pd.concat([total_shift_data,X_train])
            d.append(b)
            print(b)
#             print(total_shift_data.shape)
        new_id+=1

c:\anaconda3\lib\site-packages\ipykernel_launcher.py:5: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  """


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 337.73it/s]


label,  0 진행중
37
37
37
37
37


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 992.73it/s]


37
37
37
37
37
37
37
37
37
37


...

100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 164.72it/s]


33
33
33
33
33
33
33
33
33
33
33


100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 507.97it/s]

33
33
33
33
33
33
33
33
33
33
33


33
33
33
33
33
33
33
33



In [69]:
new_train = pd.read_csv('a.csv')

In [70]:
new_train.head()

0/0acc_x_max  0/0acc_x_min  0/0acc_x_mean  0/0acc_x_std  0/0acc_y_max  \
0      1.344268       0.59194       0.931329      0.191479      0.176871   
1      1.344268       0.59194       0.931329      0.191479      0.176871   
2      1.344268       0.59194       0.931329      0.191479      0.176871   
3      1.344268       0.59194       0.931329      0.191479      0.176871   
4      1.344268       0.59194       0.931329      0.191479      0.176871   

   0/0acc_y_min  0/0acc_y_mean  0/0acc_y_std  0/0acc_z_max  0/0acc_z_min  ...  \
0     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
1     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
2     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
3     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
4     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   

   8/8gy_x_std  8/8gy_y_max  8/8gy_y_min  8/8gy_y_mean  8/8gy_y_std  \
0    12.107143    11.936675   -54.420883     -9.147384    15.777345   
1    12.547749    38.686283   -54.420883     -2.765477    22.174348   
2    11.398581    38.686283   -54.420883      0.802384    22.485833   
3    14.327201    38.686283   -40.332241      1.981365    18.979888   
4    14.016750    38.686283   -26.146255      1.890359    17.976198   

   8/8gy_z_max  8/8gy_z_min  8/8gy_z_mean  8/8gy_z_std        label  
0    17.226521   -42.493244     -6.949288    14.330627  8/8gy_z_std  
1    34.581730   -42.493244     -2.498928    19.349135  8/8gy_z_std  
2    34.581730   -42.493244      2.357139    21.215948  8/8gy_z_std  
3    34.581730   -28.785362      6.749528    15.963473  8/8gy_z_std  
4    34.581730   -29.974279      7.834545    14.376357  8/8gy_z_std  

[5 rows x 361 columns]

In [71]:
new_train['label'] = d

In [72]:
new_train.head()

0/0acc_x_max  0/0acc_x_min  0/0acc_x_mean  0/0acc_x_std  0/0acc_y_max  \
0      1.344268       0.59194       0.931329      0.191479      0.176871   
1      1.344268       0.59194       0.931329      0.191479      0.176871   
2      1.344268       0.59194       0.931329      0.191479      0.176871   
3      1.344268       0.59194       0.931329      0.191479      0.176871   
4      1.344268       0.59194       0.931329      0.191479      0.176871   

   0/0acc_y_min  0/0acc_y_mean  0/0acc_y_std  0/0acc_z_max  0/0acc_z_min  ...  \
0     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
1     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
2     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
3     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
4     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   

   8/8gy_x_std  8/8gy_y_max  8/8gy_y_min  8/8gy_y_mean  8/8gy_y_std  \
0    12.107143    11.936675   -54.420883     -9.147384    15.777345   
1    12.547749    38.686283   -54.420883     -2.765477    22.174348   
2    11.398581    38.686283   -54.420883      0.802384    22.485833   
3    14.327201    38.686283   -40.332241      1.981365    18.979888   
4    14.016750    38.686283   -26.146255      1.890359    17.976198   

   8/8gy_z_max  8/8gy_z_min  8/8gy_z_mean  8/8gy_z_std  label  
0    17.226521   -42.493244     -6.949288    14.330627     37  
1    34.581730   -42.493244     -2.498928    19.349135     37  
2    34.581730   -42.493244      2.357139    21.215948     37  
3    34.581730   -28.785362      6.749528    15.963473     37  
4    34.581730   -29.974279      7.834545    14.376357     37  

[5 rows x 361 columns]

In [73]:
new_train.to_csv('b.csv',index = False)

In [ ]:
len(d)

In [ ]:
train_features

In [ ]:
shifted_data

In [ ]:
X_train = train_features[features].groupby('id').agg(['max', 'min', 'mean','std'])
X_train = change_col1(X_train)
for i in tn(add_col):
    X_train[i] = 0
X_train = add_FE(train_features,X_train,new_id)                   

In [ ]:
X_train['label'] = train_labels['label']

In [ ]:
test

In [ ]:
train_features

In [ ]:
X_test

In [11]:
X_test = test[features].groupby('id').agg(['max', 'min', 'mean','std'])
X_test = change_col1(X_test)
id_ = list(test['id'].unique())
for i in tn(add_col):
    X_test[i] = 0
X_test = transform(test,X_test,id_)                   

c:\anaconda3\lib\site-packages\ipykernel_launcher.py:4: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  after removing the cwd from sys.path.


c:\anaconda3\lib\site-packages\ipykernel_launcher.py:3: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  This is separate from the ipykernel package so we can avoid doing imports until


In [12]:
X_test

0/0acc_x_max  0/0acc_x_min  0/0acc_x_mean  0/0acc_x_std  0/0acc_y_max  \
id                                                                            
3125     -0.275446     -1.564000      -1.018731      0.236232      0.228040   
3126      0.627571     -1.929033      -0.522843      0.539688      1.708743   
3127      2.972063     -0.792916       0.506947      0.219934      1.941820   
3128      0.337281     -1.045889      -0.577603      0.431713     -0.258476   
3129      0.015642     -2.153047      -0.738640      0.305797      1.562602   
...            ...           ...            ...           ...           ...   
3902      0.427159     -2.050254      -0.907299      0.352604      3.057501   
3903      1.659451     -1.709527      -0.608731      0.663522      1.549890   
3904     -0.085249     -2.124959      -0.753193      0.252666      1.236138   
3905      1.438345      0.536568       0.958903      0.164880      0.076427   
3906      0.224194     -1.534616      -0.781752      0.323766      0.144179   

      0/0acc_y_min  0/0acc_y_mean  0/0acc_y_std  0/0acc_z_max  0/0acc_z_min  \
id                                                                            
3125     -0.470937      -0.019574      0.091641      0.286182     -0.573836   
3126     -0.200678       0.612161      0.333015      0.671876     -1.212052   
3127      0.219008       0.903819      0.191485      0.644154     -0.484614   
3128     -1.294482      -0.610557      0.233601      0.702574     -0.469924   
3129     -0.860883       0.182535      0.314294      1.037876     -0.631258   
...            ...            ...           ...           ...           ...   
3902     -1.414874       0.488264      0.370471      0.237183     -1.517656   
3903     -1.247963       0.371269      0.406506      0.713875     -0.996954   
3904     -0.443533       0.199782      0.300552      0.939270     -0.332901   
3905     -0.580191      -0.320975      0.120706      0.097833     -0.774209   
3906     -0.958351      -0.369244      0.219289      1.033111     -0.539595   

      ...  8/8gy_x_mean  8/8gy_x_std  8/8gy_y_max  8/8gy_y_min  8/8gy_y_mean  \
id    ...                                                                      
3125  ...     -0.723606    13.053457    49.309050   -46.629018      2.152132   
3126  ...    -28.943328    30.195351    32.005994   -22.327981      5.650735   
3127  ...      2.570501    14.988113    15.268783   -22.944503     -2.147851   
3128  ...     -4.390627     6.142258    10.813499    -3.749336      1.782493   
3129  ...      9.171516    66.221951    64.514438   -96.971316      3.437229   
...   ...           ...          ...          ...          ...           ...   
3902  ...    -21.576915    83.983583   220.936927  -187.058929     53.691867   
3903  ...     32.215360   167.368928   207.873623  -205.407503     -1.901342   
3904  ...      8.129581    13.691000    27.823478    -8.929083      7.394733   
3905  ...      4.823259    28.951632    67.359994   -67.957524     -8.147544   
3906  ...     -6.364357    17.751705    62.653680   -73.272543     -7.180805   

      8/8gy_y_std  8/8gy_z_max  8/8gy_z_min  8/8gy_z_mean  8/8gy_z_std  
id                                                                      
3125    23.651530    10.776557   -21.485650     -3.353059     7.595125  
3126    14.636147    83.342859   -99.416045     10.735902    45.868714  
3127     9.344923    60.389516   -27.233622     -3.556348    24.466871  
3128     3.624120    13.936998    -3.790100      2.074157     4.989691  
3129    37.033218    64.321940   -14.497123     10.433251    21.317281  
...           ...          ...          ...           ...          ...  
3902    98.808324   214.192019   -51.887518     51.485049    87.978381  
3903    97.793822   253.689077  -164.337764     36.861092   103.787650  
3904     9.923819    20.643944   -80.480616    -20.135285    28.841523  
3905    33.798419    40.444606   -36.637161     -0.388042    23.240182  
3906    39.261167    37.068400  -

In [13]:
X_T = train_features[features].groupby('id').agg(['max', 'min', 'mean','std'])
X_T = change_col1(X_T)
id_ = list(train_features['id'].unique())
for i in tn(add_col):
    X_T[i] = 0
X_T = transform(train_features,X_T,id_)                   

c:\anaconda3\lib\site-packages\ipykernel_launcher.py:4: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  after removing the cwd from sys.path.


c:\anaconda3\lib\site-packages\ipykernel_launcher.py:3: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  This is separate from the ipykernel package so we can avoid doing imports until


In [16]:
X_T.head()

0/0acc_x_max  0/0acc_x_min  0/0acc_x_mean  0/0acc_x_std  0/0acc_y_max  \
id                                                                          
0       1.344268      0.591940       0.931329      0.191479      0.176871   
1       1.234020     -2.156208      -0.766580      0.495528      0.700065   
2       1.219836     -1.142847       0.039836      0.711972      0.650645   
3      -0.622250     -1.417751      -0.887702      0.130899      0.283721   
4       0.599720     -2.429109      -0.659018      0.495170      1.724782   

    0/0acc_y_min  0/0acc_y_mean  0/0acc_y_std  0/0acc_z_max  0/0acc_z_min  \
id                                                                          
0      -0.624113      -0.218471      0.177131     -0.054876     -0.786336   
1      -1.295598      -0.317258      0.336415      0.888661     -1.019531   
2      -0.690990      -0.082403      0.147127      1.332992      0.073846   
3      -0.540827      -0.087668      0.194008      0.598814     -0.257124   
4      -2.055076      -0.337067      0.570305      2.678034     -1.250483   

    ...  8/8gy_x_mean  8/8gy_x_std  8/8gy_y_max  8/8gy_y_min  8/8gy_y_mean  \
id  ...                                                                      
0   ...     -4.398627    11.611743    28.697694   -54.420882     -1.899735   
1   ...    -29.533885    61.081371   100.984844  -296.239951   -102.150200   
2   ...     -9.078082    19.650804   212.598798  -157.167132     -0.142507   
3   ...     50.031590    50.356633   159.083788   -46.126730     27.694210   
4   ...     26.716478    62.620857     3.131130  -243.909948    -17.378711   

    8/8gy_y_std  8/8gy_z_max  8/8gy_z_min  8/8gy_z_mean  8/8gy_z_std  
id                                                                    
0     17.814756    32.123007   -42.493243      1.444675    16.293383  
1    108.085878   146.241141  -179.306329    -17.597961    72.460261  
2    121.092421    27.734668   -10.437208      6.306353     9.612852  
3     51.089949    35.079761   -44.693183     -8.954911    21.517674  
4     43.957594    44.374503  -270.581913     -7.726979    45.045740  

[5 rows x 360 columns]

In [17]:
add = pd.read_csv('a.csv')

In [18]:
add.head()

0/0acc_x_max  0/0acc_x_min  0/0acc_x_mean  0/0acc_x_std  0/0acc_y_max  \
0      1.344268       0.59194       0.931329      0.191479      0.176871   
1      1.344268       0.59194       0.931329      0.191479      0.176871   
2      1.344268       0.59194       0.931329      0.191479      0.176871   
3      1.344268       0.59194       0.931329      0.191479      0.176871   
4      1.344268       0.59194       0.931329      0.191479      0.176871   

   0/0acc_y_min  0/0acc_y_mean  0/0acc_y_std  0/0acc_z_max  0/0acc_z_min  ...  \
0     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
1     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
2     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
3     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
4     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   

   8/8gy_x_std  8/8gy_y_max  8/8gy_y_min  8/8gy_y_mean  8/8gy_y_std  \
0    12.107143    11.936675   -54.420883     -9.147384    15.777345   
1    12.547749    38.686283   -54.420883     -2.765477    22.174348   
2    11.398581    38.686283   -54.420883      0.802384    22.485833   
3    14.327201    38.686283   -40.332241      1.981365    18.979888   
4    14.016750    38.686283   -26.146255      1.890359    17.976198   

   8/8gy_z_max  8/8gy_z_min  8/8gy_z_mean  8/8gy_z_std        label  
0    17.226521   -42.493244     -6.949288    14.330627  8/8gy_z_std  
1    34.581730   -42.493244     -2.498928    19.349135  8/8gy_z_std  
2    34.581730   -42.493244      2.357139    21.215948  8/8gy_z_std  
3    34.581730   -28.785362      6.749528    15.963473  8/8gy_z_std  
4    34.581730   -29.974279      7.834545    14.376357  8/8gy_z_std  

[5 rows x 361 columns]

In [10]:
def transform(df,X_,id_):
    transform_data = pd.DataFrame()
    for i in tn(id_):
        tm_data = df[df['id'] == i]
        for j in [2,4,8]:
            start_num = 0
            for k in range(1,j+1):
                split_num = int(600 * k / j)
                tm_data2 = tm_data.iloc[start_num:split_num,:]
                tm_train = tm_data2[features].groupby('id').agg(['max', 'min', 'mean','std'])
    #             print(tm_train)
                tm_col = []
                for q in range(len(tm_train.columns)):
                    tm_str = str(k)+'/'+str(j)+tm_train.columns[q][0] + '_' + tm_train.columns[q][1]
                    tm_col.append(tm_str)
#                 print((tm_train))
                X_.loc[i,tm_col[0]:tm_col[-1]] = list(tm_train.iloc[0,:])
                tm_col = []

                start_num = split_num
        
    return X_

In [ ]:
X_train

In [ ]:
test

In [ ]:
X_test

In [76]:
X_T['label'] = train_labels['label']

In [77]:
X_T.head()

0/0acc_x_max  0/0acc_x_min  0/0acc_x_mean  0/0acc_x_std  0/0acc_y_max  \
id                                                                          
0       1.344268      0.591940       0.931329      0.191479      0.176871   
1       1.234020     -2.156208      -0.766580      0.495528      0.700065   
2       1.219836     -1.142847       0.039836      0.711972      0.650645   
3      -0.622250     -1.417751      -0.887702      0.130899      0.283721   
4       0.599720     -2.429109      -0.659018      0.495170      1.724782   

    0/0acc_y_min  0/0acc_y_mean  0/0acc_y_std  0/0acc_z_max  0/0acc_z_min  \
id                                                                          
0      -0.624113      -0.218471      0.177131     -0.054876     -0.786336   
1      -1.295598      -0.317258      0.336415      0.888661     -1.019531   
2      -0.690990      -0.082403      0.147127      1.332992      0.073846   
3      -0.540827      -0.087668      0.194008      0.598814     -0.257124   
4      -2.055076      -0.337067      0.570305      2.678034     -1.250483   

    ...  8/8gy_x_std  8/8gy_y_max  8/8gy_y_min  8/8gy_y_mean  8/8gy_y_std  \
id  ...                                                                     
0   ...    11.611743    28.697694   -54.420882     -1.899735    17.814756   
1   ...    61.081371   100.984844  -296.239951   -102.150200   108.085878   
2   ...    19.650804   212.598798  -157.167132     -0.142507   121.092421   
3   ...    50.356633   159.083788   -46.126730     27.694210    51.089949   
4   ...    62.620857     3.131130  -243.909948    -17.378711    43.957594   

    8/8gy_z_max  8/8gy_z_min  8/8gy_z_mean  8/8gy_z_std  label  
id                                                              
0     32.123007   -42.493243      1.444675    16.293383     37  
1    146.241141  -179.306329    -17.597961    72.460261     26  
2     27.734668   -10.437208      6.306353     9.612852      3  
3     35.079761   -44.693183     -8.954911    21.517674     26  
4     44.374503  -270.581913     -7.726979    45.045740     26  

[5 rows x 361 columns]

In [75]:
new_train.head()

0/0acc_x_max  0/0acc_x_min  0/0acc_x_mean  0/0acc_x_std  0/0acc_y_max  \
0      1.344268       0.59194       0.931329      0.191479      0.176871   
1      1.344268       0.59194       0.931329      0.191479      0.176871   
2      1.344268       0.59194       0.931329      0.191479      0.176871   
3      1.344268       0.59194       0.931329      0.191479      0.176871   
4      1.344268       0.59194       0.931329      0.191479      0.176871   

   0/0acc_y_min  0/0acc_y_mean  0/0acc_y_std  0/0acc_z_max  0/0acc_z_min  ...  \
0     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
1     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
2     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
3     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
4     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   

   8/8gy_x_std  8/8gy_y_max  8/8gy_y_min  8/8gy_y_mean  8/8gy_y_std  \
0    12.107143    11.936675   -54.420883     -9.147384    15.777345   
1    12.547749    38.686283   -54.420883     -2.765477    22.174348   
2    11.398581    38.686283   -54.420883      0.802384    22.485833   
3    14.327201    38.686283   -40.332241      1.981365    18.979888   
4    14.016750    38.686283   -26.146255      1.890359    17.976198   

   8/8gy_z_max  8/8gy_z_min  8/8gy_z_mean  8/8gy_z_std  label  
0    17.226521   -42.493244     -6.949288    14.330627     37  
1    34.581730   -42.493244     -2.498928    19.349135     37  
2    34.581730   -42.493244      2.357139    21.215948     37  
3    34.581730   -28.785362      6.749528    15.963473     37  
4    34.581730   -29.974279      7.834545    14.376357     37  

[5 rows x 361 columns]

In [78]:
all_train = pd.concat([X_T,new_train])

In [80]:
all_train.head()

0/0acc_x_max  0/0acc_x_min  0/0acc_x_mean  0/0acc_x_std  0/0acc_y_max  \
0      1.344268      0.591940       0.931329      0.191479      0.176871   
1      1.234020     -2.156208      -0.766580      0.495528      0.700065   
2      1.219836     -1.142847       0.039836      0.711972      0.650645   
3     -0.622250     -1.417751      -0.887702      0.130899      0.283721   
4      0.599720     -2.429109      -0.659018      0.495170      1.724782   

   0/0acc_y_min  0/0acc_y_mean  0/0acc_y_std  0/0acc_z_max  0/0acc_z_min  ...  \
0     -0.624113      -0.218471      0.177131     -0.054876     -0.786336  ...   
1     -1.295598      -0.317258      0.336415      0.888661     -1.019531  ...   
2     -0.690990      -0.082403      0.147127      1.332992      0.073846  ...   
3     -0.540827      -0.087668      0.194008      0.598814     -0.257124  ...   
4     -2.055076      -0.337067      0.570305      2.678034     -1.250483  ...   

   8/8gy_x_std  8/8gy_y_max  8/8gy_y_min  8/8gy_y_mean  8/8gy_y_std  \
0    11.611743    28.697694   -54.420882     -1.899735    17.814756   
1    61.081371   100.984844  -296.239951   -102.150200   108.085878   
2    19.650804   212.598798  -157.167132     -0.142507   121.092421   
3    50.356633   159.083788   -46.126730     27.694210    51.089949   
4    62.620857     3.131130  -243.909948    -17.378711    43.957594   

   8/8gy_z_max  8/8gy_z_min  8/8gy_z_mean  8/8gy_z_std  label  
0    32.123007   -42.493243      1.444675    16.293383     37  
1   146.241141  -179.306329    -17.597961    72.460261     26  
2    27.734668   -10.437208      6.306353     9.612852      3  
3    35.079761   -44.693183     -8.954911    21.517674     26  
4    44.374503  -270.581913     -7.726979    45.045740     26  

[5 rows x 361 columns]

In [79]:
import lightgbm as lgb

In [81]:
NUM_BOOST_ROUND = 1000

#######################
### FOR Stratified ####
N_SPLITS = 5
#######################
#######################

lgbm_param = {
    "objective": "multiclassova",
    'n_estimators' : NUM_BOOST_ROUND,
    "boosting": "gbdt",
#     "num_leaves": 40,
    "learning_rate": 0.01,
    "feature_fraction": 0.9,
    "reg_lambda": 2,
    "metric": "multiclass",
    "num_class" : 61,
    'seed' : 42,
}

In [82]:
all_train.shape

(20691, 361)

In [86]:
all_train.to_csv('all_train.csv',index = False)

In [87]:
X_test.to_csv('X_test.csv',index = False)

In [84]:
model_var = list(all_train.columns)
model_var.remove('label')

In [113]:
dtrain = lgb.Dataset(df.drop('label',1), df['label'])

In [98]:
all_train['label'].value_counts()

26    1518
8      388
60     336
55     333
50     333
      ... 
16     308
27     306
32     306
40     306
22     304
Name: label, Length: 61, dtype: int64

In [111]:
#DLY데이터 편중 확인 및 샘플링
# print(df['DLY'].value_counts())
df_Y = all_train[all_train['label'] == 26]
df_N = all_train[all_train['label'] != 26]
df_N_sample = df_Y.sample(frac = 0.6) #N과 Y 6대4샘플링
df = pd.concat([df_N_sample,df_N])

In [112]:
df['label'].value_counts()

26    911
8     388
60    336
55    333
50    333
     ... 
16    308
27    306
32    306
40    306
22    304
Name: label, Length: 61, dtype: int64

In [114]:
model = lgb.train(lgbm_param , dtrain) #, sample_weight=y_train.map(weights))

c:\anaconda3\lib\site-packages\lightgbm\engine.py:151: UserWarning: Found `n_estimators` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))


[LightGBM] [Info] Number of positive: 312, number of negative: 19772
[LightGBM] [Info] Number of positive: 315, number of negative: 19769
[LightGBM] [Info] Number of positive: 320, number of negative: 19764
[LightGBM] [Info] Number of positive: 322, number of negative: 19762
[LightGBM] [Info] Number of positive: 315, number of negative: 19769
[LightGBM] [Info] Number of positive: 325, number of negative: 19759
[LightGBM] [Info] Number of positive: 312, number of negative: 19772
[LightGBM] [Info] Number of positive: 312, number of negative: 19772
[LightGBM] [Info] Number of positive: 388, number of negative: 19696
[LightGBM] [Info] Number of positive: 333, number of negative: 19751
[LightGBM] [Info] Number of positive: 320, number of negative: 19764
[LightGBM] [Info] Number of positive: 322, number of negative: 19762
[LightGBM] [Info] Number of positive: 312, number of negative: 19772
[LightGBM] [Info] Number of positive: 312, number of negative: 19772
[LightGBM] [Info] Number of positi

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf


In [115]:
lgbm_valid_pred = model.predict(X_test)

In [116]:
lgbm_valid_pred.shape

(782, 61)

In [117]:
submission

id         0         1         2         3         4         5  \
0    3125  0.000033  0.000019  0.000028  0.000029  0.000043  0.000021   
1    3126  0.000227  0.000022  0.000026  0.000080  0.000030  0.000036   
2    3127  0.000058  0.011013  0.000022  0.000132  0.000055  0.000025   
3    3128  0.005315  0.000045  0.000068  0.000031  0.000034  0.000030   
4    3129  0.000202  0.000021  0.000037  0.000053  0.000215  0.000031   
..    ...       ...       ...       ...       ...       ...       ...   
777  3902  0.003219  0.000021  0.000041  0.000043  0.008858  0.000031   
778  3903  0.000073  0.000024  0.000033  0.000050  0.000069  0.000085   
779  3904  0.000262  0.000022  0.000027  0.000045  0.000040  0.000024   
780  3905  0.000034  0.000074  0.000030  0.000023  0.000021  0.000023   
781  3906  0.000101  0.000028  0.000072  0.000029  0.000040  0.000024   

            6         7         8  ...        51        52        53  \
0    0.000024  0.000025  0.000021  ...  0.000318  0.000053  0.000065   
1    0.000023  0.000047  0.000017  ...  0.000069  0.000034  0.000075   
2    0.000058  0.000100  0.000075  ...  0.000047  0.000021  0.000037   
3    0.000022  0.000071  0.000024  ...  0.000029  0.000074  0.000026   
4    0.000022  0.000031  0.000018  ...  0.000040  0.000021  0.000028   
..        ...       ...       ...  ...       ...       ...       ...   
777  0.000023  0.000041  0.000091  ...  0.000035  0.000036  0.000109   
778  0.000026  0.000040  0.000028  ...  0.000041  0.000033  0.000031   
779  0.000025  0.000026  0.000022  ...  0.000043  0.000021  0.000027   
780  0.000347  0.000046  0.000054  ...  0.000031  0.000037  0.000039   
781  0.000026  0.000037  0.000035  ...  0.000037  0.000020  0.000031   

           54        55        56        57        58        59        60  
0    0.000027  0.000026  0.000028  0.000033  0.000725  0.000022  0.000035  
1    0.000106  0.000032  0.000034  0.000174  0.000055  0.000023  0.000091  
2    0.000435  0.000035  0.000058  0.000021  0.000034  0.019032  0.000052  
3    0.000043  0.000037  0.000022  0.000142  0.000028  0.000022  0.001975  
4    0.000022  0.000033  0.000024  0.000053  0.000029  0.000023  0.000046  
..        ...       ...       ...       ...       ...       ...       ...  
777  0.000038  0.000046  0.000027  0.000079  0.000039  0.000027  0.000039  
778  0.000033  0.000043  0.000043  0.000048  0.000040  0.000028  0.000028  
779  0.000023  0.000030  0.000024  0.000279  0.000033  0.000023  0.000102  
780  0.000069  0.000027  0.000042  0.000026  0.000030  0.000043  0.000023  
781  0.000030  0.000024  0.000026  0.000259  0.000071  0.000023  0.000033  

[782 rows x 62 columns]

In [118]:
submission.iloc[:,1:] = lgbm_valid_pred
submission

id         0         1         2         3         4         5  \
0    3125  0.000033  0.000020  0.000028  0.000027  0.000042  0.000022   
1    3126  0.000363  0.000026  0.000029  0.000095  0.000037  0.000043   
2    3127  0.000068  0.008025  0.000022  0.000144  0.000067  0.000026   
3    3128  0.007874  0.000039  0.000071  0.000030  0.000035  0.000029   
4    3129  0.000221  0.000023  0.000048  0.000059  0.000372  0.000033   
..    ...       ...       ...       ...       ...       ...       ...   
777  3902  0.003399  0.000023  0.000041  0.000046  0.023336  0.000032   
778  3903  0.000100  0.000030  0.000040  0.000059  0.000089  0.000101   
779  3904  0.000459  0.000023  0.000028  0.000041  0.000053  0.000025   
780  3905  0.000033  0.000073  0.000030  0.000023  0.000022  0.000022   
781  3906  0.000149  0.000025  0.000078  0.000036  0.000046  0.000027   

            6         7         8  ...        51        52        53  \
0    0.000026  0.000025  0.000024  ...  0.000415  0.000079  0.000061   
1    0.000024  0.000053  0.000026  ...  0.000077  0.000042  0.000095   
2    0.000070  0.000093  0.000055  ...  0.000050  0.000022  0.000039   
3    0.000023  0.000167  0.000034  ...  0.000033  0.000093  0.000028   
4    0.000023  0.000034  0.000023  ...  0.000040  0.000022  0.000030   
..        ...       ...       ...  ...       ...       ...       ...   
777  0.000023  0.000044  0.000112  ...  0.000038  0.000035  0.000113   
778  0.000030  0.000043  0.000031  ...  0.000044  0.000030  0.000034   
779  0.000027  0.000029  0.000024  ...  0.000047  0.000023  0.000029   
780  0.000505  0.000051  0.000048  ...  0.000034  0.000033  0.000039   
781  0.000027  0.000042  0.000042  ...  0.000044  0.000022  0.000039   

           54        55        56        57        58        59        60  
0    0.000027  0.000028  0.000032  0.000034  0.000542  0.000023  0.000030  
1    0.000158  0.000030  0.000037  0.000257  0.000053  0.000023  0.000149  
2    0.000386  0.000038  0.000059  0.000020  0.000032  0.018762  0.000056  
3    0.000048  0.000035  0.000024  0.000144  0.000030  0.000023  0.002963  
4    0.000024  0.000034  0.000025  0.000063  0.000031  0.000023  0.000069  
..        ...       ...       ...       ...       ...       ...       ...  
777  0.000034  0.000052  0.000027  0.000108  0.000042  0.000026  0.000050  
778  0.000031  0.000044  0.000050  0.000058  0.000044  0.000028  0.000028  
779  0.000027  0.000034  0.000025  0.000424  0.000038  0.000023  0.000185  
780  0.000077  0.000032  0.000043  0.000027  0.000031  0.000047  0.000026  
781  0.000030  0.000024  0.000028  0.000767  0.000083  0.000023  0.000037  

[782 rows x 62 columns]

In [119]:
submission.to_csv('n300_lgbm_FE2.csv', index=False)

In [137]:
t = pd.read_csv('n300_lgbm_FE.csv')

In [140]:
t.iloc[:,1:].sum(1).max()

1.8369403585475939

In [126]:
t

id         0         1         2         3         4         5  \
0    3125  0.000033  0.000019  0.000028  0.000029  0.000043  0.000021   
1    3126  0.000227  0.000022  0.000026  0.000080  0.000030  0.000036   
2    3127  0.000058  0.011013  0.000022  0.000132  0.000055  0.000025   
3    3128  0.005315  0.000045  0.000068  0.000031  0.000034  0.000030   
4    3129  0.000202  0.000021  0.000037  0.000053  0.000215  0.000031   
..    ...       ...       ...       ...       ...       ...       ...   
777  3902  0.003219  0.000021  0.000041  0.000043  0.008858  0.000031   
778  3903  0.000073  0.000024  0.000033  0.000050  0.000069  0.000085   
779  3904  0.000262  0.000022  0.000027  0.000045  0.000040  0.000024   
780  3905  0.000034  0.000074  0.000030  0.000023  0.000021  0.000023   
781  3906  0.000101  0.000028  0.000072  0.000029  0.000040  0.000024   

            6         7         8  ...        51        52        53  \
0    0.000024  0.000025  0.000021  ...  0.000318  0.000053  0.000065   
1    0.000023  0.000047  0.000017  ...  0.000069  0.000034  0.000075   
2    0.000058  0.000100  0.000075  ...  0.000047  0.000021  0.000037   
3    0.000022  0.000071  0.000024  ...  0.000029  0.000074  0.000026   
4    0.000022  0.000031  0.000018  ...  0.000040  0.000021  0.000028   
..        ...       ...       ...  ...       ...       ...       ...   
777  0.000023  0.000041  0.000091  ...  0.000035  0.000036  0.000109   
778  0.000026  0.000040  0.000028  ...  0.000041  0.000033  0.000031   
779  0.000025  0.000026  0.000022  ...  0.000043  0.000021  0.000027   
780  0.000347  0.000046  0.000054  ...  0.000031  0.000037  0.000039   
781  0.000026  0.000037  0.000035  ...  0.000037  0.000020  0.000031   

           54        55        56        57        58        59        60  
0    0.000027  0.000026  0.000028  0.000033  0.000725  0.000022  0.000035  
1    0.000106  0.000032  0.000034  0.000174  0.000055  0.000023  0.000091  
2    0.000435  0.000035  0.000058  0.000021  0.000034  0.019032  0.000052  
3    0.000043  0.000037  0.000022  0.000142  0.000028  0.000022  0.001975  
4    0.000022  0.000033  0.000024  0.000053  0.000029  0.000023  0.000046  
..        ...       ...       ...       ...       ...       ...       ...  
777  0.000038  0.000046  0.000027  0.000079  0.000039  0.000027  0.000039  
778  0.000033  0.000043  0.000043  0.000048  0.000040  0.000028  0.000028  
779  0.000023  0.000030  0.000024  0.000279  0.000033  0.000023  0.000102  
780  0.000069  0.000027  0.000042  0.000026  0.000030  0.000043  0.000023  
781  0.000030  0.000024  0.000026  0.000259  0.000071  0.000023  0.000033  

[782 rows x 62 columns]

In [138]:
for i in tn(range(len(t))):
    for j in range(1,62):
        if t.iloc[i,j]>0.9:
            t.iloc[i,j] = 1

c:\anaconda3\lib\site-packages\ipykernel_launcher.py:1: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  """Entry point for launching an IPython kernel.


In [141]:
for i in tn(range(len(t))):
    for j in range(1,62):
        if t.iloc[i,j]<0.005:
            t.iloc[i,j] = 0

c:\anaconda3\lib\site-packages\ipykernel_launcher.py:1: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  """Entry point for launching an IPython kernel.


In [142]:
t.to_csv('after.csv',index = False)

In [143]:
t.sum(1)

0      3125.028923
1      3127.000000
2      3127.169393
3      3128.857142
4      3130.000000
          ...     
777    3902.509705
778    3904.000000
779    3905.000000
780    3906.000000
781    3907.000000
Length: 782, dtype: float64